In [1]:
import pandas as pd
import numpy as np
import csv
import re
import os
from textblob import TextBlob


with open('temp.csv', 'w') as w:
    with open("br.csv", encoding='utf-8') as f:
        reader = csv.reader(f)
        #Read every line of the file
        for row in reader:
            #Check if the row contains a score for reviewer rating (so we can label the review as neutral, positive, or negative)
            reviewer_rating = len(row) - 2
            if(row[reviewer_rating]):
                #Check if the row contains a written review (to train the classifier)
                review = len(row) - 1
                if(row[review]):
                    #Check if you are working with the first line so you can add a new column, "label"
                    if(row[0] == "bookID"):
                        row.append("label")
                        w.write(",".join(row))
                        w.write("\n")
                    else:
                        #Copy the existing data rows into a new csv file  
                        for i in range(0, len(row)):
                            if("," in row[i] and i != 8):
                                #Remove identifiable symbols
                                regex = re.compile('[•�,\n\[\].Ã=«*✿!·(©)"’¿“”€™?/ÃÏŸâœ@$-;:_#%&^{}+´ñÑ¨1234567890<≠>–]')
                                row[i] = regex.sub(' ', row[i])
                                try:
                                    w.write('"{}"'.format(row[i]))
                                #If the review is composed purely of non-latin alphabetic characters or if it written in a language that is not English or if its made purely of symbols e.g. "ÙŠØ³ØªØ·ÙŠØ¹ Ø§Ù„Ù†Ø¬Ø§ØØ¨Ù‡Ø§ ØŒ ÙƒØ°Ù„Ùƒ ØªØØ¯Ø« Ù‡Ø°Ø§ Ø§Ù„Ø¬Ø²Ø¡ Ø¹Ù† Ù…Ø±Ø¶" then leave the review column empty
                                except ValueError:
                                    print("Line with bookID", row[0], "was not copied because of illegal characters.")    
                            elif(i == 8):
                                row[i] = row[i].replace("'ll", " will")
                                row[i]  = row[i].replace("'ve", " have")
                                row[i]  = row[i].replace("'d", " would")
                                row[i]  = row[i].replace("'m", " am")
                                row[i]  = row[i].replace("'re", " are")
                                row[i]  = row[i].replace("n't", " not")
                                #Remove identifiable symbols
                                regex = re.compile('[•�,\n\[\].Ã=«*✿!·(©)"’¿“”€™?/ÃÏŸâœ@$-;:_#%&^{}+´ñÑ¨1234567890<≠>–]')
                                row[i] = regex.sub(' ', row[i])
                                try:
                                    w.write(row[i])
                                #If the review is composed purely of non-latin alphabetic characters or if it written in a language that is not English or if its made purely of symbols e.g. "ÙŠØ³ØªØ·ÙŠØ¹ Ø§Ù„Ù†Ø¬Ø§ØØ¨Ù‡Ø§ ØŒ ÙƒØ°Ù„Ùƒ ØªØØ¯Ø« Ù‡Ø°Ø§ Ø§Ù„Ø¬Ø²Ø¡ Ø¹Ù† Ù…Ø±Ø¶" then leave the review column empty
                                except ValueError:
                                    print("Line with bookID", row[0], "was not copied because of illegal characters.")    
                            else:
                                try:
                                    w.write(row[i])
                                #If the review is composed purely of non-latin alphabetic characters or if it written in a language that is not English or if its made purely of symbols e.g. "ÙŠØ³ØªØ·ÙŠØ¹ Ø§Ù„Ù†Ø¬Ø§ØØ¨Ù‡Ø§ ØŒ ÙƒØ°Ù„Ùƒ ØªØØ¯Ø« Ù‡Ø°Ø§ Ø§Ù„Ø¬Ø²Ø¡ Ø¹Ù† Ù…Ø±Ø¶" then leave the review column empty
                                except ValueError:
                                    print("Line with bookID", row[0], "was not copied because of illegal characters.")                              
                            w.write(",")
                        #Label each row, if the reviewer rating is 3 then neutral, if more positive, if less negative   
                        if(int(row[reviewer_rating]) == 3):
                            w.write("0")
                        elif(int(row[reviewer_rating]) > 3):
                            w.write("1")
                        elif(int(row[reviewer_rating]) < 3):
                            w.write("-1")
                        w.write("\n")
                        
print("Parsing Terminated.")
with open('dataset.csv', "w") as w:
    with open('temp.csv') as f:
        reader = csv.reader(f)
        positive_reviews_count = 0
        negative_reviews_count = 0
        neutral_reviews_count = 0
        total_number_of_words_in_negative_reviews = 0
        total_number_of_words_in_positive_reviews = 0
        total_number_of_words_in_neutral_reviews = 0
        for row in reader:
            #Check if the row contains a written review (to train the classifier)
            review = len(row) - 2
            label = len(row) - 1
            if(row[review].split() != "".split()):
                #Add that row to our final dataset
                print("Wait, we're copying line with bookID", row[0])
                if(row[label] == '1'):
                    positive_reviews_count = 1 + positive_reviews_count
                    total_number_of_words_in_positive_reviews = len(row[review].split()) + total_number_of_words_in_positive_reviews
                elif(row[label] == '0'):
                    neutral_reviews_count = 1 + neutral_reviews_count
                    total_number_of_words_in_neutral_reviews = len(row[review].split()) + total_number_of_words_in_neutral_reviews
                elif(row[label] == '-1'):
                    negative_reviews_count = 1 + negative_reviews_count
                    total_number_of_words_in_negative_reviews = len(row[review].split()) + total_number_of_words_in_negative_reviews
                for i in range(0, len(row) - 1):
                    if("," in row[i]):
                        w.write('"{}"'.format(row[i]))
                    else:
                        w.write(row[i])
                    w.write(",")
                w.write(row[len(row) - 1])
                w.write("\n")
                
row_count = positive_reviews_count + negative_reviews_count + neutral_reviews_count
print("\nDataset ready.")
os.remove("temp.csv")
print("\nStatistics:")
print("Number of positive reviews in dataset:", positive_reviews_count)
print("Number of negative reviews in dataset:", negative_reviews_count)
print("Number of neutral reviews in dataset:", neutral_reviews_count)
print("Total number of rows in dataset:", row_count) #The first row with the column names doesn't count
print("Total number of words in positive reviews:", total_number_of_words_in_positive_reviews)
print("Total number of words in negative reviews:", total_number_of_words_in_negative_reviews)
print("Total number of words in neutral reviews:", total_number_of_words_in_neutral_reviews)
print("Total number of words in reviews:", total_number_of_words_in_positive_reviews + total_number_of_words_in_negative_reviews + total_number_of_words_in_neutral_reviews)


Line with bookID 5488 was not copied because of illegal characters.
Line with bookID 9484 was not copied because of illegal characters.
Line with bookID 8741 was not copied because of illegal characters.
Line with bookID 8742 was not copied because of illegal characters.
Line with bookID 1883 was not copied because of illegal characters.
Line with bookID 8506 was not copied because of illegal characters.
Line with bookID 6482251 was not copied because of illegal characters.
Line with bookID 6482251 was not copied because of illegal characters.
Line with bookID 3258 was not copied because of illegal characters.
Line with bookID 9993 was not copied because of illegal characters.
Line with bookID 9996 was not copied because of illegal characters.
Line with bookID 5164 was not copied because of illegal characters.
Line with bookID 2879 was not copied because of illegal characters.
Line with bookID 6984 was not copied because of illegal characters.
Line with bookID 407 was not copied becaus

Line with bookID 3083 was not copied because of illegal characters.
Line with bookID 4731 was not copied because of illegal characters.
Line with bookID 5882 was not copied because of illegal characters.
Line with bookID 3178 was not copied because of illegal characters.
Line with bookID 343 was not copied because of illegal characters.
Line with bookID 435 was not copied because of illegal characters.
Line with bookID 2722 was not copied because of illegal characters.
Line with bookID 7441 was not copied because of illegal characters.
Line with bookID 8153 was not copied because of illegal characters.
Line with bookID 2159 was not copied because of illegal characters.
Line with bookID 2159 was not copied because of illegal characters.
Line with bookID 9584 was not copied because of illegal characters.
Line with bookID 9584 was not copied because of illegal characters.
Line with bookID 3203 was not copied because of illegal characters.
Line with bookID 1327 was not copied because of il

Line with bookID 3408 was not copied because of illegal characters.
Line with bookID 1424 was not copied because of illegal characters.
Line with bookID 3804 was not copied because of illegal characters.
Line with bookID 3710 was not copied because of illegal characters.
Line with bookID 5425 was not copied because of illegal characters.
Line with bookID 4728 was not copied because of illegal characters.
Line with bookID 4728 was not copied because of illegal characters.
Line with bookID 6789 was not copied because of illegal characters.
Line with bookID 7643 was not copied because of illegal characters.
Line with bookID 213667 was not copied because of illegal characters.
Line with bookID 4730 was not copied because of illegal characters.
Line with bookID 4729 was not copied because of illegal characters.
Line with bookID 3751 was not copied because of illegal characters.
Line with bookID 4987 was not copied because of illegal characters.
Line with bookID 6595 was not copied because o

Line with bookID 13400 was not copied because of illegal characters.
Line with bookID 12857 was not copied because of illegal characters.
Line with bookID 11055 was not copied because of illegal characters.
Line with bookID 14118 was not copied because of illegal characters.
Line with bookID 12094 was not copied because of illegal characters.
Line with bookID 12627 was not copied because of illegal characters.
Line with bookID 11198 was not copied because of illegal characters.
Line with bookID 12435 was not copied because of illegal characters.
Line with bookID 11442 was not copied because of illegal characters.
Line with bookID 13596 was not copied because of illegal characters.
Line with bookID 13601 was not copied because of illegal characters.
Line with bookID 13599 was not copied because of illegal characters.
Line with bookID 13600 was not copied because of illegal characters.
Line with bookID 13598 was not copied because of illegal characters.
Line with bookID 13597 was not cop

Line with bookID 13892 was not copied because of illegal characters.
Line with bookID 13929 was not copied because of illegal characters.
Line with bookID 13241 was not copied because of illegal characters.
Line with bookID 13241 was not copied because of illegal characters.
Line with bookID 12377 was not copied because of illegal characters.
Line with bookID 12829 was not copied because of illegal characters.
Line with bookID 206625 was not copied because of illegal characters.
Line with bookID 232708 was not copied because of illegal characters.
Line with bookID 1220952 was not copied because of illegal characters.
Line with bookID 1220952 was not copied because of illegal characters.
Line with bookID 15682 was not copied because of illegal characters.
Line with bookID 15687 was not copied because of illegal characters.
Line with bookID 15687 was not copied because of illegal characters.
Line with bookID 15263 was not copied because of illegal characters.
Line with bookID 15953 was n

...

Wait, we're copying line with bookID 335385
Wait, we're copying line with bookID 335309
Wait, we're copying line with bookID 334863
Wait, we're copying line with bookID 335387
Wait, we're copying line with bookID 334865
Wait, we're copying line with bookID 334904
Wait, we're copying line with bookID 334901
Wait, we're copying line with bookID 334902
Wait, we're copying line with bookID 335322
Wait, we're copying line with bookID 335321
Wait, we're copying line with bookID 334804
Wait, we're copying line with bookID 335320
Wait, we're copying line with bookID 334799
Wait, we're copying line with bookID 335325
Wait, we're copying line with bookID 335333
Wait, we're copying line with bookID 334999
Wait, we're copying line with bookID 334995
Wait, we're copying line with bookID 334970
Wait, we're copying line with bookID 335328
Wait, we're copying line with bookID 334951
Wait, we're copying line with bookID 769000
Wait, we're copying line with bookID 334971
Wait, we're copying line with bo

Wait, we're copying line with bookID 345173
Wait, we're copying line with bookID 336765
Wait, we're copying line with bookID 337000
Wait, we're copying line with bookID 345179
Wait, we're copying line with bookID 336994
Wait, we're copying line with bookID 345178
Wait, we're copying line with bookID 336998
Wait, we're copying line with bookID 341202
Wait, we're copying line with bookID 336999
Wait, we're copying line with bookID 345084
Wait, we're copying line with bookID 341201
Wait, we're copying line with bookID 336909
Wait, we're copying line with bookID 341105
Wait, we're copying line with bookID 336910
Wait, we're copying line with bookID 341108
Wait, we're copying line with bookID 345224
Wait, we're copying line with bookID 345225
Wait, we're copying line with bookID 336766
Wait, we're copying line with bookID 1420161
Wait, we're copying line with bookID 345105
Wait, we're copying line with bookID 345107
Wait, we're copying line with bookID 336784
Wait, we're copying line with b

Wait, we're copying line with bookID 337418
Wait, we're copying line with bookID 345670
Wait, we're copying line with bookID 345667
Wait, we're copying line with bookID 337378
Wait, we're copying line with bookID 345676
Wait, we're copying line with bookID 337463
Wait, we're copying line with bookID 345675
Wait, we're copying line with bookID 337493
Wait, we're copying line with bookID 341753
Wait, we're copying line with bookID 341752
Wait, we're copying line with bookID 341751
Wait, we're copying line with bookID 341890
Wait, we're copying line with bookID 337466
Wait, we're copying line with bookID 341896
Wait, we're copying line with bookID 341895
Wait, we're copying line with bookID 341892
Wait, we're copying line with bookID 341891
Wait, we're copying line with bookID 341894
Wait, we're copying line with bookID 341793
Wait, we're copying line with bookID 337465
Wait, we're copying line with bookID 341804
Wait, we're copying line with bookID 337482
Wait, we're copying line with bo

Wait, we're copying line with bookID 346470
Wait, we're copying line with bookID 342429
Wait, we're copying line with bookID 338051
Wait, we're copying line with bookID 346472
Wait, we're copying line with bookID 342488
Wait, we're copying line with bookID 346469
Wait, we're copying line with bookID 346471
Wait, we're copying line with bookID 338119
Wait, we're copying line with bookID 338118
Wait, we're copying line with bookID 338121
Wait, we're copying line with bookID 342497
Wait, we're copying line with bookID 338131
Wait, we're copying line with bookID 346476
Wait, we're copying line with bookID 338129
Wait, we're copying line with bookID 346484
Wait, we're copying line with bookID 338132
Wait, we're copying line with bookID 342455
Wait, we're copying line with bookID 338120
Wait, we're copying line with bookID 346475
Wait, we're copying line with bookID 338133
Wait, we're copying line with bookID 338064
Wait, we're copying line with bookID 346450
Wait, we're copying line with bo

Wait, we're copying line with bookID 347443
Wait, we're copying line with bookID 347462
Wait, we're copying line with bookID 343402
Wait, we're copying line with bookID 343323
Wait, we're copying line with bookID 347461
Wait, we're copying line with bookID 347463
Wait, we're copying line with bookID 339149
Wait, we're copying line with bookID 347467
Wait, we're copying line with bookID 339150
Wait, we're copying line with bookID 339146
Wait, we're copying line with bookID 1017221
Wait, we're copying line with bookID 347475
Wait, we're copying line with bookID 339017
Wait, we're copying line with bookID 343332
Wait, we're copying line with bookID 347486
Wait, we're copying line with bookID 347478
Wait, we're copying line with bookID 343331
Wait, we're copying line with bookID 343333
Wait, we're copying line with bookID 347489
Wait, we're copying line with bookID 339046
Wait, we're copying line with bookID 339045
Wait, we're copying line with bookID 347281
Wait, we're copying line with b